In [15]:

from dotenv import load_dotenv
from langchain.llms import AzureOpenAI
from langchain.chat_models import AzureChatOpenAI
from langchain.prompts import PromptTemplate
from langchain.indexes import VectorstoreIndexCreator #vector database
from datetime import datetime
from langchain.chat_models import openai
import requests

import os


os.environ["AZURE_OPENAI_KEY"] = "cba90ab54d5d49cab7406de3e9f19faa"
os.environ["AZURE_OPENAI_ENDPOINT"] = "https://lab-ai-openai-eus.openai.azure.com/"




In [16]:

from openai import AzureOpenAI


client = AzureOpenAI(
  azure_endpoint = "https://lab-ai-openai-eus.openai.azure.com/", 
  api_key=os.getenv("OPENAI_API_KEY"),  
  api_version="2024-02-15-preview"
)


message_text = [{"role":"system","content":"You are an AI assistant that helps people find information."}]

azure_model = client.chat.completions.create(
    model="gpt-35-turbo", # model = "deployment_name"
    messages = message_text,
   temperature=0.7,
  max_tokens=800,
  top_p=0.95,
  frequency_penalty=0,
  presence_penalty=0,
  stop=None

)

In [17]:
#upload pdf 

from langchain_community.document_loaders import DirectoryLoader

directory_path = "certifdocs"

loader = DirectoryLoader(directory_path)
pages = loader.load_and_split()
pages


[Document(page_content='Microsoft Azure training and certifications\n\naka.ms/AzureTrainCertDeck\n\nTable of contents\n\nThis guide has been created to provide training and certification options to achieve personal success.\n\nHow to use this deck\n\nTraining Journeys\n\nAzure training journey for IT pros Azure training journey for developers Azure training journey for data & AI pros\n\nCertifications\n\nMicrosoft Azure certifications Azure Fundamentals Azure Data Fundamentals Azure AI Fundamentals Azure Administrator Associate Azure Security Engineer Associate Azure Stack Hub Operator Associate Azure Network Engineer Associate Windows Server Hybrid Administrator Associate Azure Solutions Architect Expert Azure for SAP Workloads Specialty\n\nContinue your Azure training journey Microsoft Azure Virtual Training Days\n\nAzure Virtual Desktop Specialty Azure Developer Associate DevOps Engineer Expert Azure IoT Developer Specialty Azure Database Administrator Associate Azure Data Engineer 

RAG : recherche par similarité (en utilisant les embeddings)

Extract text from pdf 

In [18]:
from pdfminer.high_level import extract_text
import os 


dirs = os.listdir(directory_path)
output = "pdftotext.txt"
for file in dirs:
    path_file = os.path.join(directory_path,file)
    print(path_file)
    text = extract_text(path_file)
    with open(output, 'a',encoding='utf-8') as fichier:
        fichier.write(text)




certifdocs\Azure-Training---Certification-Guide_94751.pdf
certifdocs\How To Apply Your 100% Discounted Voucher Code .pdf


In [19]:
from langchain.document_loaders import TextLoader,DirectoryLoader

loader = TextLoader("pdftotext.txt")
documents= loader.load()
len(documents)


1

In [20]:
documents

[Document(page_content='Microsoft Azure \ntraining and certifications\n\naka.ms/AzureTrainCertDeck\n\n\x0cTable of \ncontents \n\nThis guide has been \ncreated to provide \ntraining and \ncertification options \nto achieve personal \nsuccess.\n\nHow to use this deck\n\nTraining Journeys\n\nAzure training journey for IT pros\nAzure training journey for developers\nAzure training journey for data & AI pros\n\nCertifications\n\nMicrosoft Azure certifications\nAzure Fundamentals\nAzure Data Fundamentals\nAzure AI Fundamentals\nAzure Administrator Associate\nAzure Security Engineer Associate\nAzure Stack Hub Operator Associate\nAzure Network Engineer Associate\nWindows Server Hybrid Administrator Associate\nAzure Solutions Architect Expert\nAzure for SAP Workloads Specialty\n\nContinue your Azure training journey\nMicrosoft Azure Virtual Training Days\n\nAzure Virtual Desktop Specialty\nAzure Developer Associate\nDevOps Engineer Expert\nAzure IoT Developer Specialty\nAzure Database Administ

In [21]:
#chunk_size  
chunk_size = 1000
chunk_overlap = 120 #duplication des informations entre les vecteurs coupés 

In [22]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
text_splitter = RecursiveCharacterTextSplitter(chunk_size=chunk_size, chunk_overlap=chunk_overlap)
chunks = text_splitter.split_documents(documents)

print(len(chunks)) # 15 vecteurs

4166


In [23]:
chunks[35].page_content 


'Get started at\naka.ms/AzureCerts_StackHubOperator\n\nStart here\nDecide if this is the right certification for you\n\nUpskill with recommended training and experience\n\nPass required exam to earn your certification\n\nThis certification is a good fit if your  \nresponsibilities include:\n\nâ€¢ Plan, deploy, package, update, and maintain the Azure \n\nStack Hub infrastructure. \n\nâ€¢ Offer hybrid cloud resources and requested services \nand manage infrastructure as a service (IaaS) and \nplatform as a service (PaaS).\n\nFirst, make sure your skills are up to date.\n\nNeed to update your skills in Azure  \nadministration?\nAzure Administrator training on  \nMicrosoft Learn.\n\nExam AZ-600  \nConfiguring and Operating a \nHybrid Cloud with Microsoft \nAzure Stack Hub\n\nSkills outline guide\n\nâ€¢ AZ-600\n\nSelf-paced online learning\nMicrosoft Learn\n\nInstructor-led training  \nCourse AZ-600T00: Configuring \nand Operating a Hybrid Cloud \nwith Microsoft Azure Stack Hub\n\nAdditiona

In [24]:
#from langchain.embeddings import OpenAIEmbeddings
#import numpy as np
#from langchain.vectorstores import Chroma
#import time



#embeddings = OpenAIEmbeddings(deployment_id="text-embedding-ada-002",chunk_size="100")
#docsearch = Chroma.from_documents(chunks, embeddings)
#for splitted_document in chunks:
 #   Chroma.from_documents(documents=[splitted_document], embedding=embeddings)
  #  time.sleep(60)

In [25]:
from langchain.embeddings import OpenAIEmbeddings
from langchain_community.vectorstores import FAISS


embeddings = OpenAIEmbeddings(deployment_id="text-embedding-ada-002",chunk_size="50")

#faiss_vectorstore= FAISS.from_documents(documents, embeddings) : Limite de tokens !!! 


Enregistrer les chunks en tant que vecteur en utilisant faiss  
pour résoudre le problème des tokens appels nombreux API, on découpe les chunks
 en blocs , sleep 
save le tout en local pour ne pas relancer à chaque fois

In [26]:
from langchain_community.vectorstores import FAISS
from time import sleep

from langchain.embeddings import AzureOpenAIEmbeddings

embeddings = AzureOpenAIEmbeddings(
   
azure_deployment= "text-embedding-ada-002"
)

# Iterate over each chunk of documents
bloc = 40
for i in range(0, len(chunks), bloc):
    print(i)
    faiss_vectorstore= FAISS.from_documents(chunks[i:i+bloc], embeddings)
    sleep(10)
    print(faiss_vectorstore)
    faiss_retriever = faiss_vectorstore.as_retriever()
    faiss_vectorstore.save_local("faiss_index")


#optimiser la taille des chunks plus tard 




0


40
80
120
160
200
240
280
320
360
400
440
480
520
560
600
640
680
720
760
800
840
880
920
960
1000
1040
1080
1120
1160
1200
1240
1280
1320
1360
1400
1440
1480
1520
1560
1600
1640
1680
1720
1760
1800
1840
1880
1920
1960
2000
2040
2080
2120
2160
2200
2240
2280
2320
2360
2400
2440
2480
2520
2560
2600
2640
2680
2720
2760
2800
2840
2880
2920
2960
3000
3040
3080
3120
3160
3200
3240
3280
3320
3360
3400
3440
3480
3520
3560
3600
3640
3680
3720
3760
3800
3840
3880
3920
3960
4000
4040
4080
4120
4160


Retrievers are used to find relevant documents or passages that contain the answer to a given query.
The system "retrieves" any documents that could be relevant in answering the question, and then passes those documents (along with the original question) to the language model for a "generation" step.

La question est posée en utilisant le chat,
toujours en utilisant la similarité sématique 


Test utilisant LCEL


In [27]:
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser


template_context1 =  """answer the question only according to the context  : {context}
            Question: {question}
        """
template_context2= """answer the question only according to the 429 th line and the lines just after of the file  : {context}
            Question: {question}
        """

prompt = ChatPromptTemplate.from_template(template_context1) #creer un chat prompt 

retrieval_chain = (
    {"context": faiss_retriever, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)
retrieval_chain.invoke("quelles sont  les certifications Associate? et quel est leur nombre? ")



NameError: name 'llm' is not defined

In [32]:
# RetrievalQA
from langchain.chains import RetrievalQA
import faiss 
from langchain_openai import AzureChatOpenAI
llm = AzureChatOpenAI(deployment_name="gpt-35-turbo",openai_api_version="2024-02-15-preview",temperature = "0.0")
# trouver comment load faiss_retriever = index = faiss.read_index( "faiss_index") index.as_retriever()



qa_stuff = RetrievalQA.from_chain_type( #creer une chain pour répondre à la question
    llm=llm, 
    chain_type="stuff", # tous les documents d'un coup et les passe au LLM
    retriever=faiss_retriever, 
    return_source_documents= True,
    verbose=True
)

In [33]:

query = "what is a voucher code?"
result = qa_stuff.invoke(query)
result



> Entering new RetrievalQA chain...

> Finished chain.


{'query': 'what is a voucher code?',
 'result': 'A voucher code is a code that can be used to obtain a discount or a free product or service. In the context of the provided text, a voucher code is used to obtain a 100% discount on a Microsoft certification exam when scheduling it through Pearson VUE. The voucher code is obtained from the Voucher Management team and needs to be applied during the checkout process to bring the total cost to zero.',
 'source_documents': [Document(page_content='times. Our consultants have obtained the latest industry and security certifications from other cloud service providers such as \n\nMicrosoft, Hadoop, Sitecore, Adobe. This document is meant to serve as a quick reference guide for applying your voucher \n\ncode at Pearson VUE   \n\nApplying your Voucher Code at Pearson VUE \n\nThe following steps will show you how to schedule your Microsoft certification exam with your 100% discounted voucher code. \n\nAfter March 1, 2023, Avanade no longer uses the

Préparer un golden dataset 


In [34]:
questions = ["Quel est le nombre  des certifications Azure ? ","Quel est le nombre des certifications Associate?", "qu est ce qu un voucher en un mot"]
ground_truths = [["Il y a 15 certifications Azure"],
                 ["Il y a 10 certifications Assiociate mentionnees"], 
                 ["une promotion"]
                ]
results = []
contexts = []


for query in questions:  #generer les results
    result = qa_stuff({"query": query})
    results.append(result['result']) 
    sources = result["source_documents"]
    contents = [source.page_content for source in sources]  

    processed_contents = []
    for content in contents:
        if isinstance(content, str):  
          
            processed_content = content.split('.')[:2]  
            processed_contents.extend(processed_content)  
        else:
    
            print(f"Expected a string but got {type(content)}") 
    contexts.append(processed_contents)

print(results)
print(contexts)


c:\Users\liticia.ouahioune\AppData\Local\Programs\Python\Python310\lib\site-packages\langchain_core\_api\deprecation.py:119: LangChainDeprecationWarning: The method `Chain.__call__` was deprecated in langchain 0.1.0 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(




> Entering new RetrievalQA chain...

> Finished chain.


> Entering new RetrievalQA chain...

> Finished chain.


> Entering new RetrievalQA chain...

> Finished chain.
["Le texte ne fournit pas d'information sur le nombre de certifications Azure.", "Je suis désolé, mais je ne peux pas répondre à cette question car il n'y a pas suffisamment d'informations dans le contexte fourni pour déterminer de quelles certifications Associate il s'agit. Veuillez fournir plus de détails ou de contexte pour que je puisse vous aider de manière plus précise.", 'Coupon.']
[['times', ' Our consultants have obtained the latest industry and security certifications from other cloud service providers such as \n\nMicrosoft, Hadoop, Sitecore, Adobe', 'Avanade email', ' Select the Microsoft Certifications tile to begin scheduling your exam', 'â€¢  Use OnVUE â€“ Online at my home or office', ' \n\n       Global Learning   \n\n9', '3 \n\n \n \n \n \n  \n \n \n   \n \n \n\x0c6', ' \n\nIn the Discounts window, yo

In [36]:
# Creating a DataFrame
data = {
    'question': questions,
    'answer': results,
    'contexts': contexts,
    'ground_truth': ground_truths
}

df = pd.DataFrame(data)

# Display the DataFrame
print(df)

                                           question  \
0   Quel est le nombre  des certifications Azure ?    
1  Quel est le nombre des certifications Associate?   
2                 qu est ce qu un voucher en un mot   

                                              answer  \
0  Le texte ne fournit pas d'information sur le n...   
1  Je suis désolé, mais je ne peux pas répondre à...   
2                                            Coupon.   

                                            contexts  \
0  [times,  Our consultants have obtained the lat...   
1  [Avanade email,  Select the Microsoft Certific...   
2  [3 \n\n \n \n \n \n  \n \n \n   \n \n \n6,  \...   

                                        ground_truth  
0                   [Il y a 15 certifications Azure]  
1  [Il y a 10 certifications Assiociate mentionnees]  
2                                    [une promotion]  


Evaluer


In [37]:
import pandas as pd 
from datasets import Dataset
from tqdm import tqdm
import pyarrow as py
import pyarrow as pa
import pyarrow.dataset as ds
from ragas import evaluate
from ragas.metrics import  faithfulness, answer_relevancy, context_recall
from ragas.llms import LangchainLLMWrapper
from datasets import Dataset, Features, Sequence, Value



# Définir le dataset explicitement 
features = Features({
    "question": Value("string"),
    "answer": Value("string"),
    "contexts": Sequence(Value("string")),
    "ground_truth": Value("string")
})
dataset = Dataset.from_dict(df, features=features)



ragas_vertexai_llm = LangchainLLMWrapper(llm)

evaluate_result = evaluate(
       dataset = dataset , metrics = [faithfulness, answer_relevancy,  context_recall],
        llm=ragas_vertexai_llm,
)


Evaluating:   0%|          | 0/9 [00:00<?, ?it/s]No statements were generated from the answer.
No statements were generated from the answer.
Evaluating:   0%|          | 0/9 [00:01<?, ?it/s]
Exception in thread Thread-6:
Traceback (most recent call last):
  File "c:\Users\liticia.ouahioune\AppData\Local\Programs\Python\Python310\lib\threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "c:\Users\liticia.ouahioune\AppData\Local\Programs\Python\Python310\lib\site-packages\ragas\executor.py", line 96, in run
    results = self.loop.run_until_complete(self._aresults())
  File "c:\Users\liticia.ouahioune\AppData\Local\Programs\Python\Python310\lib\asyncio\base_events.py", line 649, in run_until_complete
    return future.result()
  File "c:\Users\liticia.ouahioune\AppData\Local\Programs\Python\Python310\lib\site-packages\ragas\executor.py", line 84, in _aresults
    raise e
  File "c:\Users\liticia.ouahioune\AppData\Local\Programs\Python\Python310\lib\site-packages\ragas\execu

ExceptionInRunner: The runner thread which was running the jobs raised an exeception. Read the traceback above to debug it. You can also pass `raise_exceptions=False` incase you want to show only a warning message instead.


Test2 : Préparer un Golden Dataset 


In [ ]:
import pandas as pd 
from datasets import Dataset
from tqdm import tqdm
import pyarrow as py

questions = ["Quelles sont toutes les certifications Associate? ","Quel est le nombre des certifications Associate?"]
ground_truths = [["Azure Administrator (AZ-104)","Azure Security Engineer (AZ-500)","Azure Stack Hub Operator (AZ-600)","Azure Developer (AZ-204)","Azure Database Administrator (DP-300)","Azure Data Engineer (DP-203)","Data Analyst (DA-100)","Azure AI Engineer (AI-102)","Azure Data Scientist (DP-100)","Azure Network Engineer (AZ-700)","Windows Server Hybrid Administrator (AZ-800 + AZ-801)"],["Il y a 10 certifications Assiociate mentionnees"]]
answers = []
contexts = []
grount_t = []
grounded_t = []

for query in questions: 
  answers.append(retrieval_chain.invoke(query))
  #  contexts.append(faiss_retriever.get_relevant_documents(query) )
  contexts.append(faiss_retriever.get_relevant_documents(query))
 # print(contextDoc)
 

rag_dataset =[]
context_ext = []
contexts_ext=[]

for i in range(len(ground_truths[1])): 
       ground_t=  ground_truths[1][i]
       grounded_t.append(ground_t)


for i in range(len(contexts[1])): 
       context_ext=  contexts[1][i].page_content
       contexts_ext.append(context_ext)

dict = {'questions': questions[1],
       'ground_truths ': ground_t,
       'answers': answers[1],
       'contexts': context_ext}


print(dict)
#dataset = Dataset.from_pandas(df)


{'questions': 'Quel est le nombre des certifications Associate?', 'ground_truths ': 'Il y a 10 certifications Assiociate mentionnees', 'answers': 'Réponse: Il y a une certification Associate mentionnée dans le document, la certification Microsoft Certified: Azure Data Scientist Associate.', 'contexts': 'Azure Data Scientists implement and run machine learning workloads on Microsoft Azure Machine Learning.  \n\nExplore recommended training resources that will help you prepare for required exams.\n\nInstructor-led  \ntraining\n\nDesigning and Implementing a \nData Science Solution on Azure\nDP-100T01 | 3 days\n\nAND\n\nImplementing a Machine Learning Solution \nwith Microsoft Azure Databricks\nDP-090T00 | 1 day\n\nCreate machine \nlearning models\n5 modules\n\nSelf-paced online  \ntraining on  \nMicrosoft Learn\n\nBuild and operate machine \nlearning solutions with Azure \nMachine Learning\n15 modules\n\nMicrosoft Azure AI \nFundamentals: Explore visual \ntools for machine learning\n4 mo

In [ ]:
import os
import pyarrow as pa
import pyarrow.dataset as ds
import pandas as pd
from datasets import Dataset
from ragas import evaluate
from ragas.metrics import  faithfulness, answer_relevancy, context_recall


print(dict)
#dataset = Dataset.from_dict(dict)
#print(dataset)
#score = evaluate(dataset,metrics=[faithfulness, answer_relevancy,  context_recall])
#score_df = score.to_pandas()
#score_df.to_csv("EvaluationScores.csv", encoding="utf-8", index=False)


#eval_dataset = pd.DataFrame.from_dict(dict,orient='columns',dtype='object')
#eval_dataset.to_csv("evaluation_dataset.csv")


<class 'dict'>


faire un fichier d'extraction json pour utiliser ragas
context
question
reponse


Test 2 : Evaluer

In [ ]:
from ragas import evaluate
from ragas.metrics import  faithfulness, answer_relevancy, context_recall





def evaluate_ragas (ragas_dataset):
    metrics = [
    faithfulness,
    answer_relevancy,
     context_recall,
    ]
    for m in metrics : 
        print(m.name)

    results = evaluate(ragas_dataset, metrics)
    return results

c:\Users\liticia.ouahioune\AppData\Local\Programs\Python\Python310\lib\site-packages\langchain_core\_api\deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.0.10 and will be removed in 0.2.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import ChatOpenAI`.
  warn_deprecated(


In [ ]:
basic_qa_result = evaluate_ragas(dataset)
basic_qa_result


faithfulness
answer_relevancy
context_recall


AttributeError: 'pyarrow._dataset.InMemoryDataset' object has no attribute 'features'